In [1]:
from web2json.preprocessor import *
from web2json.ai_extractor import *
from web2json.postprocessor import *
from web2json.pipeline import *

In [2]:
import dotenv
dotenv.load_dotenv()

True

In [3]:
llm = NvidiaLLMClient(config={'api_key': os.getenv('NVIDIA_API_KEY'),'model_name': 'qwen/qwen2.5-7b-instruct'})

In [4]:
prompt_template = """
You are a helpful assistant that extracts structured data from web pages.
You will be given a web page and you need to extract the following information:
{content}

schema: {schema}
Please provide the extracted data in JSON format.
WITH ONLY THE FIELDS THAT ARE IN THE SCHEMA.
"""

In [5]:
classification_prompt_template = """
# HTML Chunk Relevance Classification Prompt

You are an HTML content classifier. Your task is to analyze an HTML chunk against a given schema and determine if the content is relevant.

## Instructions:
1. Carefully examine the provided HTML chunk
2. Compare it against the given schema/criteria
3. Determine if the HTML chunk contains content that matches or is relevant to the schema
4. Respond with ONLY a JSON object containing a single field "relevant" with value 1 (relevant) or 0 (not relevant)

## Input Format:
**Schema/Criteria:**
{schema}

**HTML Chunk:**
```html
{content}
```

## Output Format:
Your response must be ONLY a valid JSON object with no additional text:

```json
{{
  "relevant": 1
}}
```

OR

```json
{{
  "relevant": 0
}}
```

## Classification Rules:
- Output 1 if the HTML chunk contains content that matches the schema criteria
- Output 0 if the HTML chunk does not contain relevant content
- Consider semantic meaning, not just exact keyword matches
- Look at text content, attributes, structure, and context
- Ignore purely structural HTML elements (like divs, spans) unless they contain relevant content
- Be STRICT in your evaluation - only mark as relevant (1) if there is clear, meaningful content that directly relates to the schema
- Empty elements, placeholder text, navigation menus, headers/footers, and generic UI components should typically be marked as not relevant (0)
- The HTML chunk does not need to contain ALL schema information, but it must contain SUBSTANTIAL and SPECIFIC content related to the schema

CRITICAL: Your entire response MUST be exactly one JSON object. DO NOT include any explanations, reasoning, markdown formatting, code blocks, or additional text. Output ONLY the raw JSON object.
"""

In [6]:
pre = BasicPreprocessor(config={'keep_tags':True})
# llm = GeminiLLMClient(config={'api_key': os.getenv('GEMINI_API_KEY'),})
# ai = AIExtractor(llm_client=llm ,prompt_template=prompt_template)
ai = LLMClassifierExtractor(llm_client=llm, prompt_template=prompt_template, classifier_prompt=classification_prompt_template)
post = PostProcessor()

In [7]:
pipe = Pipeline(preprocessor=pre, ai_extractor=ai, postprocessor=post)

In [8]:
from pydantic import BaseModel, Field, constr, condecimal

class ProductModel(BaseModel):
    productTitle: constr(min_length=1, max_length=200) = Field(
        ...,
        title="Product Title",
        description="The full title of the product"
    )
    price: condecimal(gt=0, decimal_places=2) = Field(
        ...,
        title="Product Price",
        description="Unit price (must be > 0, two decimal places)."
    )
    manufacturer: constr(min_length=1, max_length=1000) = Field(
        ...,
        title="Manufacturer",
        description="Name of the product manufacturer."
    )

    

In [9]:
config = {
    'keep_tags': True,
}

In [16]:
url = "https://www.amazon.com/Instant-Pot-Multi-Use-Programmable-Pressure/dp/B00FLYWNYQ?_encoding=UTF8&content-id=amzn1.sym.2f889ce0-246f-467a-a086-d9a721167240&dib=eyJ2IjoiMSJ9.2EzBddTDEktLY8ckTsraM_cZ6pzKuNkA6y_gLR0-Uz1ekttQU6tuQEcjb8PThy0PfhvxLqeYWh3N7pQrGgRxAWzapVklC_aU6xBzD-3Wwqx3qyQRHsmOhPRsSpeCOIIZqS3SKDowZEPYrGnCbRMt5vxnsYMW-fD-zBbgeoeGYmbsN2U6_HNhLjrpePKCbQPmnZBJ9UhgYE4fE3DVuYm8xlJe9l5GixDLVFtZUq4m5FE.Ol-jiuu9P6mQie0yXLJj-Ht5-TXmIXuRPije85p_YVo&dib_tag=se&keywords=cooker&pd_rd_r=2cede598-f3ae-49ca-8a46-e5945a9c2631&pd_rd_w=2HLSC&pd_rd_wg=ZyUUn&qid=1749508157&sr=8-3"
schema = ProductModel  # pydantic class

# read html file 
# with open(r'C:\Users\abdfa\Desktop\UNI STUFFING\GRADUATION PROJECT\Group Work\MCP_WEB2JSON\0000.htm', 'r', encoding='utf-8') as file:
#     content = file.read()

# with open(r'C:\Users\abdfa\Desktop\UNI STUFFING\GRADUATION PROJECT\Group Work\MCP_WEB2JSON\Amazon.com_ Instant Pot Duo 7-in-1 Electric Pressure Cooker, Slow Cooker, Rice Cooker, Steamer, Sauté, Yogurt Maker, Warmer & Sterilizer, Includes App With Over 800 Recipes, Stainless Steel, 6 Quart.htm', 'r', encoding='utf-8') as file:
#     content = file.read()


In [23]:
pipe.run(content=url,is_url=True, schema=schema)

Preprocessed content: <!DOCTYPE html>
<html>
<head>
<link>
<link>
<link>
<meta><title>Amazon.com: Instant Pot Duo 7-in-1 Electric Pressure Cooker, Slow Cooker, Rice Cooker, Steamer, Sauté, Yogurt Maker, Warmer &amp; Sterilizer, Includes App With Over 800 Recipes, Stainless Steel, 6 Quart</title>
</meta></link></link></link></head>
<body><div>
<button>
  Shortcuts menu
</button>
<nav>
<h2>Skip to</h2>
<ul>
<li>
        Main content
</li>
<li>
        About this item
</li>
<li>
        About this item
</li>
<li>
        About this item
</li>
<li>
        Buying options
</li>
<li>
        Compare with similar items
</li>
<li>
        Videos
</li>
<li>
        Reviews
</li>
</ul>
<h2>
      Keyboard shortcuts
  </h2>
<ul>
<li>
Search
alt
+
/
</li>
<li>
Cart
shift
+
alt
+
C
</li>
<li>
Home
shift
+
alt
+
H
</li>
<li>
Orders
shift
+
alt
+
O
</li>
<li>
<button>
<div>
<span>Add to cart</span>
<div>
<span>shift</span>
<span>+</span>
<span>alt</span>
<span>+</span>
<span>K</span>
</div>
</div>
</

{'productTitle': 'Amazon.com: Instant Pot Duo 7-in-1 Electric Pressure Cooker, Slow Cooker, Rice Cooker, Steamer, Sauté, Yogurt Maker, Warmer & Sterilizer, Includes App With Over 800 Recipes, Stainless Steel, 6 Quart',
 'price': 99.95,
 'manufacturer': 'Instant Pot'}